# **Taller 1 de Sistemas Basados en Geolocalización**

## Introducción
Este taller tiene como objetivo aplicar conceptos de geolocalización y cálculo de distancias utilizando la fórmula de Haversine. Además, se explorará la variación del área de la Laguna de Fúquene a lo largo del tiempo para evaluar su impacto en la delimitación de terrenos y desplazamiento de poblaciones. Los resultados deberán ser sustentados mediante mapas dinámicos y análisis comparativos.

---

## Profesor: Carlos Armando López Solano, MSc.

### 1. Cálculo de distancias con la fórmula de Haversine
Desarrolle un sistema de software que, mediante el uso de la fórmula de Haversine, calcule la distancia en cada caso:

| Caso | Φ₁ (Latitud 1) | λ₁ (Longitud 1) | Φ₂ (Latitud 2) | λ₂ (Longitud 2) |
|------|---------------|---------------|---------------|---------------|
| 1    | 4.6369566546922485 | -74.08344303563474 | 4.698387290122269 | -74.08913229761984 |
| 2    | 2.4930822620498403 | -76.56469927139997 | 4.553288632232513 | -75.65871130171998 |
| 3    | 7.141088134111742 | -73.11869057856512 | 42.35927858183055 | -71.09328053009632 |

Luego, compare el resultado obtenido con la medición de dicha distancia utilizando el mapa dinámico de su preferencia.

#### Preguntas:
- ¿Qué ubicaciones corresponden a las coordenadas dadas?
- ¿Qué conclusión puede sacar de estas mediciones?

---

In [109]:
# Import Required Libraries

# Import folium library for creating maps
import folium
import math

In [110]:
class Coordenada:
    def __init__(self,city:str,name:str,latitude:float,longitude:float):
        self.city = city
        self.name = name
        self.latitude = latitude
        self.longitude = longitude
        
    def get_latitude(self):
        return self.latitude
    
    def get_longitude(self):
        return self.longitude
    
    def __str__(self):
        return f"City: {self.city}, Name: {self.name}, Latitude: {self.latitude}, Longitude: {self.longitude}"
    

class TierraPlana:
    def __init__(self):
        self.coordenadas = []
        
    def agregar_coordenada(self, coordenada:Coordenada):
        self.coordenadas.append(coordenada)
        
    def distancia_entre_coordenadas(self,coordenada1:Coordenada,coordenada2:Coordenada) -> float:
        return self.haversine(coordenada1.get_latitude(),coordenada1.get_longitude(),coordenada2.get_latitude(),coordenada2.get_longitude())
    
    def get_coordenada(self,name:str) -> Coordenada:     
        for coordenada in self.coordenadas:
            if coordenada.name == name:
                return coordenada
        return None

    def radio_tierra_en_latitud(self, lat:float) -> float:
        a = 6378.137  #Radius at sea level at equator
        b = 6356.752  #Radius at poles
        
        c = (a**2*math.cos(lat))**2
        d = (b**2*math.sin(lat))**2
        e = (a*math.cos(lat))**2
        f = (b*math.sin(lat))**2
        
        return math.sqrt((c+d)/(e+f))

    def haversine(self, Lat1:float,Lon1:float,lat2:float,lon2:float) -> float:
        # El radio lo calculamos con el prodmedio de las latitudes
        R = self.radio_tierra_en_latitud((Lat1+lat2)/2)
        
        # Calculamos la formula de haversine
        dLat = math.radians(lat2 - Lat1)
        dLon = math.radians(lon2 - Lon1)
        a = math.sin(dLat/2) * math.sin(dLat/2) + math.cos(math.radians(Lat1)) * math.cos(math.radians(lat2)) * math.sin(dLon/2) * math.sin(dLon/2)
        c = 2*R*math.atan(math.sqrt(a))
        return c
    
    def mostrar_coordenadas(self):
        for coordenada in self.coordenadas:
            print(coordenada)

class Mapa:
    def crear_mapa(self,coordenada1:Coordenada,coordenada2:Coordenada):
        
        distancia_coordenadas = TierraPlana().distancia_entre_coordenadas(coordenada1,coordenada2)
        if distancia_coordenadas < 100:
            zoom = 12
        elif distancia_coordenadas < 300:
            zoom = 8
        else:
            zoom = 3
        
        dlat = (coordenada1.get_latitude() + coordenada2.get_latitude())/2
        dlon = (coordenada1.get_longitude() + coordenada2.get_longitude())/2
        
        map_osm = folium.Map(location=[dlat, dlon], zoom_start=zoom)
        
        folium.Marker(
            location=[coordenada1.get_latitude(), coordenada1.get_longitude()],
            popup=f"{coordenada1.city} - {coordenada1.name}"
        ).add_to(map_osm)

        folium.Marker(
            location=[coordenada2.get_latitude(), coordenada2.get_longitude()],
            popup=f"{coordenada2.city} - {coordenada2.name}"
        ).add_to(map_osm)
        
        folium.PolyLine(
            locations=[[coordenada1.get_latitude(),coordenada1.get_longitude()],[coordenada2.get_latitude(),coordenada2.get_longitude()]],
            color="#FF0000",
            weight=5,
            tooltip="Distancia: {:.2f} km".format(distancia_coordenadas),
        ).add_to(map_osm)
        return map_osm



In [120]:
casos = [
    {"city": "Bogota", "name":"Universidad Nacional", "latitude": 4.6369566546922485, "longitude": -74.08344303563474 },
    {"city": "Bogota", "name":"Universidad Uniminuto", "latitude": 4.698387290122269, "longitude": -74.08913229761984 },
    {"city": "Popayan", "name":"Casa de mi EX", "latitude": 2.4930822620498403, "longitude": -76.56469927139997},
    {"city": "Armenia", "name":"Universidad del Quindio", "latitude": 4.553288632232513, "longitude": -75.65871130171998},
    {"city": "Bucaramanga", "name":"Universidad industrial de Santander", "latitude": 7.141088134111742, "longitude": -73.11869057856512},
    {"city": "Boston", "name":"Massachusetts institute of technology", "latitude": 42.35927858183055 , "longitude": -71.09328053009632}

]

tierra_plana = TierraPlana()

coordenadas = []

for caso in casos:
    coordenada = Coordenada(caso["city"],caso["name"], caso["latitude"], caso["longitude"])
    tierra_plana.agregar_coordenada(coordenada)


### **Caso 1**

In [112]:
cordenada1 = tierra_plana.get_coordenada("Universidad Nacional")
cordenada2 = tierra_plana.get_coordenada("Universidad Uniminuto")
distancia_coordenadas = tierra_plana.distancia_entre_coordenadas(cordenada1,cordenada2) 

print(f"La distancia entre las siguientes coordenadas es {distancia_coordenadas:.2f} KM")
print(cordenada1)
print(cordenada2)

miMapa = Mapa()
miMapa.crear_mapa(cordenada1,cordenada2)

La distancia entre las siguientes coordenadas es 6.84 KM
City: Bogota, Name: Universidad Nacional, Latitude: 4.6369566546922485, Longitude: -74.08344303563474
City: Bogota, Name: Universidad Uniminuto, Latitude: 4.698387290122269, Longitude: -74.08913229761984


### **Caso 2**

In [113]:
cordenada3 = tierra_plana.get_coordenada("Casa de mi EX")
cordenada4 = tierra_plana.get_coordenada("Universidad del Quindio")
distancia_coordenadas = tierra_plana.distancia_entre_coordenadas(cordenada3,cordenada4) 

print(f"La distancia entre las siguientes coordenadas es {distancia_coordenadas:.2f} KM")
print(cordenada3)
print(cordenada4)

miMapa = Mapa()
miMapa.crear_mapa(cordenada3,cordenada4)

La distancia entre las siguientes coordenadas es 250.29 KM
City: Popayan, Name: Casa de mi EX, Latitude: 2.4930822620498403, Longitude: -76.56469927139997
City: Armenia, Name: Universidad del Quindio, Latitude: 4.553288632232513, Longitude: -75.65871130171998


### **Caso 3**

In [121]:
cordenada5 = tierra_plana.get_coordenada("Universidad industrial de Santander")
cordenada6 = tierra_plana.get_coordenada("Massachusetts institute of technology")
distancia_coordenadas = tierra_plana.distancia_entre_coordenadas(cordenada5,cordenada6) 

print(f"La distancia entre las siguientes coordenadas es {distancia_coordenadas:.2f} KM")
print(cordenada5)
print(cordenada6)

miMapa = Mapa()
miMapa.crear_mapa(cordenada5,cordenada6)

La distancia entre las siguientes coordenadas es 3750.07 KM
City: Bucaramanga, Name: Universidad industrial de Santander, Latitude: 7.141088134111742, Longitude: -73.11869057856512
City: Boston, Name: Massachusetts institute of technology, Latitude: 42.35927858183055, Longitude: -71.09328053009632



### 2. Análisis del área de la Laguna de Fúquene
La Laguna de Fúquene tiene un área que varía cada dos décadas, contrayéndose y expandiéndose.

Para ayudar a los gobernadores de Boyacá y Cundinamarca a tomar decisiones sobre el desplazamiento de campesinos y la delimitación de fincas, se solicita determinar el porcentaje del área de crecimiento de la laguna (diferencia entre las áreas máxima y mínima). Pueden utilizar el método que deseen. 

#### Requisitos:
- Presentar el resultado final en un mapa dinámico.
- Sustentar el análisis con datos y metodología utilizada.

---

## **Caso de prueba finca Mundo Nuevo**

En este caso se realiza la prueba en un terreno practicamente rectangular en donde se realizo la validacion de los calculos.

In [115]:
import pandas as pd
import folium
import random
import geopy.distance
from shapely.geometry import Point, Polygon

def get_coordenadas_csv(ruta_cordenadas:str) -> list:
    """Obtiene las coordenadas de un archivo CSV y lo devuelve en una lista de tuplas

    Args:
        ruta_cordenadas (str): Ruta del archivo con las coordenadas

    Returns:
        list: Lista de tuplas que contienen las coordenadas
    """
    df = pd.read_csv(ruta_cordenadas)
    coordenadas = list(zip(df["LATITUDE"], df["LONGITUDE"]))
    return coordenadas

def get_area_montecarlo(coordenadas:list,num_puntos:int=10_000) -> dict:
    """Obtiene un diccionario con la informacion relacionada al calculo del area con el metodo de montecarlo

    Args:
        coordenadas (list): Lista de coordenadas
        num_puntos (int, optional): Determina el numero de puntos aleatorios con los cuales se calcula el area. Defaults to 10_000.

    Returns:
        dict: {
            'puntos_aleatoreos':lista_puntos_aleatoreos,
            'area_rectangulo':area_total_km2,
            'area_aproximada':area_aprox_km2,
            'poligono':poligono
        }
    """
    
    # Creamos el poligono geoespacial
    poligono = Polygon(coordenadas)
    
    # Determinar los límites del área
    latitudes, longitudes = zip(*coordenadas)
    min_lat, max_lat = min(latitudes), max(latitudes)
    min_lon, max_lon = min(longitudes), max(longitudes)

    # Generar puntos aleatorios dentro del área delimitada y contar los que caen dentro del polígono
    puntos_dentro = 0
    lista_puntos_aleatoreos = []
    
    for _ in range(num_puntos):
        rand_lat = random.uniform(min_lat, max_lat)
        rand_lon = random.uniform(min_lon, max_lon)
        punto = Point(rand_lat, rand_lon)
        lista_puntos_aleatoreos.append((rand_lat, rand_lon))
        if poligono.contains(punto):
            puntos_dentro += 1

    # Calcular el área aproximada con Montecarlo
    area_total_km2 = (geopy.distance.geodesic((min_lat, min_lon), (max_lat, min_lon)).km *
                    geopy.distance.geodesic((min_lat, min_lon), (min_lat, max_lon)).km)
    
    area_aprox_km2 = (puntos_dentro / num_puntos) * area_total_km2

    return  {
        'puntos_aleatoreos':lista_puntos_aleatoreos,
        'area_rectangulo':area_total_km2,
        'area_aproximada':area_aprox_km2,
        'poligono':poligono
    }
    
def draw_map_montecarlo(coordenadas:list,poligono:Polygon,puntos_aleatoreos:list):
    """Muestra el mapa con los puntos aleatoreos del calculo de montecarlo

    Args:
        coordenadas (list): Lista de coordenadas [(lat1,lat1),(lat2,lat2)]
        poligono (Polygon): Objeto Polygon construido con las coordenadas
        puntos_aleatoreos (list): Lista de puntos aleatoreos

    """
    latitudes, longitudes = zip(*coordenadas)
    latutud_promedio = sum(latitudes)/len(latitudes)
    longitud_promedio = sum(longitudes)/len(longitudes)
    
    mapa = folium.Map(location=[latutud_promedio, longitud_promedio], zoom_start=20)

    folium.Polygon(locations=coordenadas, color="blue", fill=True, fill_opacity=0.4).add_to(mapa)

    for lat,lon in puntos_aleatoreos:
        if poligono.contains(Point(lat,lon)):
            folium.CircleMarker(location=[lat,lon], radius=2, color='red', fill=True, fill_opacity=0.1).add_to(mapa)

    #te amo mi amor jejejeje
    
    # Mostrar mapa
    return mapa 
    
# Defino la ruta del archivo de coordenadas
ruta_cordenadas = "../files/coordenadas_pesqueras.csv"

# Optenemos la lista de coordenadas 
coordenadas = get_coordenadas_csv(ruta_cordenadas)

# Definimos numero de puntos aleatores 
N = 1000

dict_retorno = get_area_montecarlo(coordenadas,N)

mapa = draw_map_montecarlo(coordenadas,dict_retorno["poligono"],dict_retorno["puntos_aleatoreos"])

print(f"El area del terreno ubicado en la Vereda Mundo nuevo")
print(f"Area total del rectangulo de referencia: {dict_retorno["area_rectangulo"]:.4f} km2")
print(f"Area aproximada del terreno con {N} puntos aleatoreos: {dict_retorno["area_aproximada"]:.4f} km2")

mapa

El area del terreno ubicado en la Vereda Mundo nuevo
Area total del rectangulo de referencia: 0.0021 km2
Area aproximada del terreno con 1000 puntos aleatoreos: 0.0018 km2


In [116]:

ruta_cordenadas = "../files/coordenadas_cancha_campin.csv"

# Optenemos la lista de coordenadas 
coordenadas = get_coordenadas_csv(ruta_cordenadas)

# Definimos numero de puntos aleatores 
N = 10_000

dict_retorno = get_area_montecarlo(coordenadas,N)

mapa = draw_map_montecarlo(coordenadas,dict_retorno["poligono"],dict_retorno["puntos_aleatoreos"])

print(f"El area del terreno ubicado en la Vereda Mundo nuevo")
print(f"Area total del rectangulo de referencia: {dict_retorno["area_rectangulo"]:.4f} km2")
print(f"Area aproximada del terreno con {N} puntos aleatoreos: {dict_retorno["area_aproximada"]:.4f} km2")

mapa

El area del terreno ubicado en la Vereda Mundo nuevo
Area total del rectangulo de referencia: 0.0090 km2
Area aproximada del terreno con 10000 puntos aleatoreos: 0.0071 km2


## **Caso de la laguna de fuquene**

In [117]:
ruta_cordenadas_laguna_actual = "../files/coordenadas_laguna_fuquene_actual.csv"
ruta_cordenadas_laguna_maxima = "../files/coordenadas_laguna_fuquene_max.csv"

coordenadas_laguna_actual = get_coordenadas_csv(ruta_cordenadas_laguna_actual)
coordenadas_laguna_maxima = get_coordenadas_csv(ruta_cordenadas_laguna_maxima)

# Definimos numero de puntos aleatores 
N = 10_000

dict_area_laguna_actual = get_area_montecarlo(coordenadas_laguna_actual,N)
dict_area_laguna_maxima = get_area_montecarlo(coordenadas_laguna_maxima,N)

area_maxima = dict_area_laguna_maxima["area_aproximada"]
area_actual = dict_area_laguna_actual["area_aproximada"]
area_crecimiento = area_maxima - area_actual
porcentaje_crecimiento = (area_crecimiento * 100) / area_maxima

print(f"El area de la laguna de Fuquene:")
print(f"El area total de la laguna en su maxima amplitud es de: {area_maxima:.2f} km2")
print(f"El area total de la laguna en su amplitud actual es de: {area_actual:.2f} km2")
print(f"El area de crecimiento de esta laguna es: {area_crecimiento:.2f} km2 un porcentaje estimado de {porcentaje_crecimiento:.2f}%")


El area de la laguna de Fuquene:
El area total de la laguna en su maxima amplitud es de: 30.70 km2
El area total de la laguna en su amplitud actual es de: 10.25 km2
El area de crecimiento de esta laguna es: 20.45 km2 un porcentaje estimado de 66.60%


In [118]:
# Definimos un punto medio en las coordenadas de la laguna
latitudes, longitudes = zip(*coordenadas_laguna_maxima)
latutud_promedio = sum(latitudes)/len(latitudes)
longitud_promedio = sum(longitudes)/len(longitudes)

# Definimos el mapa
mapa = folium.Map(location=[latutud_promedio, longitud_promedio], zoom_start=13)

# Definimos y agregamos el primer poligono de la laguna en su maxima amplitud
folium.Polygon(locations=coordenadas_laguna_maxima, color="green", fill=True, fill_opacity=0.4).add_to(mapa)
folium.Polygon(locations=coordenadas_laguna_actual, color="blue", fill=True, fill_opacity=1).add_to(mapa)

mapa 

In [119]:

puntos_aleatoreos_laguna_maxima = dict_area_laguna_maxima['puntos_aleatoreos'] 
puntos_aleatoreos_laguna_actual = dict_area_laguna_actual['puntos_aleatoreos'] 
poligono_laguna_maxima = dict_area_laguna_maxima['poligono']
poligono_laguna_actual = dict_area_laguna_actual['poligono']

# Definimos el mapa
mapa_crecimiento = folium.Map(location=[latutud_promedio, longitud_promedio], zoom_start=13)

# Definimos y agregamos el primer poligono de la laguna en su maxima amplitud
folium.Polygon(locations=coordenadas_laguna_maxima, color="green", fill=False, fill_opacity=0.4).add_to(mapa_crecimiento)


for lat,lon in puntos_aleatoreos_laguna_maxima:
    if not poligono_laguna_actual.contains(Point(lat,lon)) and poligono_laguna_maxima.contains(Point(lat,lon)):
        folium.CircleMarker(location=[lat,lon], radius=2, color='red', fill=True, fill_opacity=0.4).add_to(mapa_crecimiento)
        
mapa_crecimiento

---
## Bibliografía sugerida
- J. A. E. García Álvarez, “ASÍ FUNCIONA EL GPS,” 2015. [Online]. Available: [https://goo.gl/eXsp7K](https://goo.gl/eXsp7K). [Accessed: 25-Feb-2017].
- C. Beatty, “Location-Based Services: Navigation for the Masses, At Last!,” Journal of Navigation, 30-May-2002. [Online]. Available: [https://goo.gl/uXwEwI](https://goo.gl/uXwEwI). [Accessed: 12-Apr-2017].